In [ ]:
# Folium for visualization
#!pip install folium

In [ ]:
import os
import sys

import requests
from bs4 import BeautifulSoup
from glob import glob

import geopandas

from shapely.geometry import LineString
from shapely.ops import cascaded_union

import folium
from folium.plugins import Fullscreen, MarkerCluster

In [2]:
# NOAA file download URL
noaa_base_url = 'https://www.nhc.noaa.gov/gis/'

# Hurricane Maria Identifier
hurricane_id = 'al15' 
hurricane_year = '2017'
file_format = '{}_5day'.format(hurricane_id + hurricane_year)

In [5]:
def get_links(hurricane_id):
    noaa_request = requests.get(noaa_base_url + 'archive_forecast_results.php?id=' + hurricane_id)

    soup = BeautifulSoup(noaa_request.content, 'html.parser')

    # Grab all links on web-page that have href attribute 
    links = soup.findAll('a', href=True)  
  
    # Filter the link sending with .mp4  
    hurricane_links = [noaa_base_url + link['href'] for link in links if file_format in link['href']]  
  
    return hurricane_links

def download_file(link, folder):
    file = requests.get(link).content
    name = link.split('/')[-1]
    save_path = os.path.join(folder, name)

    print("Saving file:", save_path)
    with open(save_path, 'wb') as fp:
        fp.write(file)    

In [6]:
# Get all relevant download links
links = get_links(hurricane_id)

# Create the folder if necessary
folder = os.path.abspath(os.path.join('../data/hurricane-gis', file_format))
if not os.path.exists(folder): os.makedirs(folder)

# Download the files
for link in set(links):
    download_file(link, folder)

Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_040A.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_058.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_041.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_037A.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_046A.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_024A.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_007A.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_020A.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day

Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_044.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_008A.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_048.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_017.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_026A.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_007.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_050.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al152017_5day_009A.zip
Saving file: /Users/nitinserro/Desktop/MIDS/w210-bluetarp/data/hurricane-gis/al152017_5day/al

In [9]:
# Adapted from https://gist.github.com/rsignell-usgs/b02b326cc7b0db53bea01ccff5b31ff4
# Warning cones, hurricane track points
cones, points = [], []

for fname in sorted(glob(os.path.join(folder, '{}_*.zip'.format(file_format)))):
    number = os.path.splitext(os.path.split(fname)[-1])[0].split('_')[-1]
    pgn = geopandas.read_file(
        '/{}-{}_5day_pgn.shp'.format(hurricane_id + hurricane_year, number),
        vfs='zip://{}'.format(fname)
    )
    cones.append(pgn)

    pts = geopandas.read_file(
        '/{}-{}_5day_pts.shp'.format(hurricane_id + hurricane_year, number),
        vfs='zip://{}'.format(fname)
    )
    # Grab only the first point
    points.append(pts.iloc[0])

/Users/nitinserro/anaconda3/lib/python3.6/site-packages/fiona/env.py:409: FionaDeprecationWarning: The vfs keyword argument is deprecated. Instead, pass a URL that uses a zip or tar (for example) scheme.
  return f(*args, **kwargs)


In [10]:
# Colors for the hurricane track
colors = {
    'Subtropical Depression': 'yellow',
    'Tropical Depression': 'yellow',
    'Tropical Storm': 'orange',
    'Subtropical Storm': 'orange',
    'Hurricane': 'red',
    'Major Hurricane': 'crimson'
}

In [11]:
# Combine the last_cone and the track
last_cone = cones[-1]['geometry'].iloc[0]
track = LineString([point['geometry'] for point in points])
polygon = cascaded_union([last_cone, track])

# Derive bounding box from the track and the latest prediction cone.
bbox = polygon.buffer(2).bounds

In [15]:
# Folium visualization
lon = track.centroid.x
lat = track.centroid.y

m = folium.Map(location=[lat, lon], tiles='OpenStreetMap', zoom_start=4)

Fullscreen(position='topright', force_separate_button=True).add_to(m)

marker_cluster0 = MarkerCluster(name='Observations')
marker_cluster1 = MarkerCluster(name='Past predictions')

marker_cluster0.add_to(m)
marker_cluster1.add_to(m)

def style_function(feature):
    return {
        'fillOpacity': 0,
        'color': 'black',
        'stroke': 1,
        'weight': 0.5,
        'opacity': 0.2,
    }

# Highlight cone prediction roughly over PR
latest = cones[30]
folium.GeoJson(
    data=latest.__geo_interface__,
    name='Cone prediction as of {}'.format(latest['ADVDATE'].values[0]),
).add_to(m)

# Past cone predictions
for cone in cones[:-1]:
    folium.GeoJson(
        data=cone.__geo_interface__,
        style_function=style_function,
    ).add_to(marker_cluster1)

# Latest points prediction
for k, row in pts.iterrows():
    date = row['FLDATELBL']
    hclass = row['TCDVLP']
    location = row['LAT'], row['LON']
    popup = '{}<br>{}'.format(date, hclass)
    folium.CircleMarker(
        location=location,
        radius=10,
        fill=True,
        color=colors[hclass],
        popup=popup,
    ).add_to(m)

# All the points along the track
for point in points:
    date = point['FLDATELBL']
    hclass = point['TCDVLP']
    location = point['LAT'], point['LON']
    popup = '{}<br>{}'.format(date, hclass)
    folium.CircleMarker(
        location=location,
        radius=5,
        fill=True,
        color=colors[hclass],
        popup=popup,
    ).add_to(m)
    
m